In [1]:
import tqdm as notebook_tqdm
import torch
from transformers import AutoTokenizer, AutoModelForSeq2SeqLM
from datasets import load_dataset
from sacrebleu.metrics import BLEU
from tqdm import tqdm
import sentencepiece as spm
import ctranslate2

/root/.cache/pypoetry/virtualenvs/zindi-LtLKIbXv-py3.9/lib/python3.9/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
# %cd /home/rana/Projects/zindi
%cd /root/zindi/
import yaml
with open('common/config.yaml', 'r') as f:
    config = yaml.load(f, Loader=yaml.SafeLoader)

checkpoint = config.get('checkpoint')
new_model_path=config.get('new_model_path')+checkpoint
ct_model_path=config.get('ct_model_path')+checkpoint

/root/zindi


/root/.cache/pypoetry/virtualenvs/zindi-LtLKIbXv-py3.9/lib/python3.9/site-packages/IPython/core/magics/osm.py:417: UserWarning: using dhist requires you to install the `pickleshare` library.
  self.shell.db['dhist'] = compress_dhist(dhist)[-100:]


In [6]:
### Eval ct model

device = "cuda" if torch.cuda.is_available() else "cpu"
print(f"Using device: {device}")

sp_source_model = spm.SentencePieceProcessor(model_file=ct_model_path+'/sentencepiece.bpe.model')
sp_target_model = spm.SentencePieceProcessor(model_file=ct_model_path+'/sentencepiece.bpe.model')


def translate(translator, text):
    tokens = sp_source_model.encode(text, out_type=str)
    # print(tokens)
    tokens = ['dyu'] + tokens + ["</s>"] +['fr']
    try:
        results = translator.translate_batch([tokens])
        # The translated results are token strings, so we need to convert them to IDs before decoding
        translations = []
        for translation in results:
            decoded_text = sp_target_model.decode(translation.hypotheses[0])
            translations.append(decoded_text)
    except Exception as e:
        print(f"Translation error: {e}")
        translations = [""]  # Return empty string if translation fails
    return translations

def calculate_bleu(references, hypotheses):
    bleu = BLEU()
    return bleu.corpus_score(hypotheses, [references]).score

def validate_model(model_path, dataset_name, split):
    # Load CTranslate2 model
    translator = ctranslate2.Translator(model_path, device=device)
    # Load dataset
    dataset = load_dataset(dataset_name, split=split)
    # Translate and calculate BLEU score
    hypotheses = []
    references = []

    for batch in tqdm(dataset, desc="Translating"):
        source_text = batch['translation']['dyu']  # Adjust this based on your dataset's column names
        reference = batch['translation']['fr']  # Adjust this based on your dataset's column names
        
        # translation = translate(translator, tokenizer, source_text, device)[0]
        # tokenizer=None
        translation = translate(translator, source_text)[0].replace("fr ","")
        hypotheses.append(translation)
        references.append(reference)
        print(translation, "----", reference)
        # break

    bleu_score = calculate_bleu(references, hypotheses)
    print(f"BLEU Score: {bleu_score:.2f}")

validate_model(ct_model_path, "uvci/Koumankan_mt_dyu_fr", "validation")

Using device: cuda


Translating:   0%|          | 5/1471 [00:00<01:07, 21.79it/s]

eng_Latn I'm called Bi cogodɔ ⁇ fr. ---- Tu portes un nom de fantaisie.
eng_Latn The first seven points. ---- Trois points d’avance.
eng_Latn The sun will shine. ---- Le soleil s’est couché.
eng_Latn One way⁇  ---- Mêmes mouvements.
por_Latn N ma daraka dun ban.⁇  ---- Je n’ai pas encore déjeuné.


Translating:   1%|          | 8/1471 [00:00<01:08, 21.27it/s]

eng_Latn A ⁇  y again to open n.fr. ---- Arrêtez de vous moquer de moi.
eng_Latn Four of them are American. ---- Je suis Américain.
eng_Latn I am a member of parliament. ---- Merci, monsieur le député
eng_Latn Jan and his father lon⁇  ---- Jean n’a pas connu son père.
eng_Latn An account can be found in the website. ---- Il faudra rentrer dedans.


...

Translating:   1%|          | 17/1471 [00:00<01:26, 16.82it/s]

eng_Latn Some of the bonds are in the area. ---- D’autres maisons plus jaunes.
por_Latn O que é que se passa com um homem que não é um homem? ---- Ce coureur était le combien ?
eng_Latn I've been seen with a few of them. ---- J'étais à deux pas.


Translating:   1%|▏         | 19/1471 [00:01<01:26, 16.74it/s]

eng_Latn I'm not sure I'm going to be able to do it myself. ---- J'ouvre la porte.
eng_Latn Yes, it is a good idea. ---- Et pourquoi donc ?


KeyboardInterrupt: 

In [ ]:
validate_model(ct_model_path, "uvci/Koumankan_mt_dyu_fr", "train")

Translating:  15%|█▌        | 1238/8065 [00:00<00:01, 5796.11it/s]

Translation error: translate_batch(): incompatible function arguments. The following argument types are supported:
    1. (self: ctranslate2._ext.Translator, source: List[List[str]], target_prefix: Optional[List[Optional[List[str]]]] = None, *, max_batch_size: int = 0, batch_type: str = 'examples', asynchronous: bool = False, beam_size: int = 2, patience: float = 1, num_hypotheses: int = 1, length_penalty: float = 1, coverage_penalty: float = 0, repetition_penalty: float = 1, no_repeat_ngram_size: int = 0, disable_unk: bool = False, suppress_sequences: Optional[List[List[str]]] = None, end_token: Optional[Union[str, List[str], List[int]]] = None, return_end_token: bool = False, prefix_bias_beta: float = 0, max_input_length: int = 1024, max_decoding_length: int = 256, min_decoding_length: int = 1, use_vmap: bool = False, return_scores: bool = False, return_attention: bool = False, return_alternatives: bool = False, min_alternative_expansion_prob: float = 0, sampling_topk: int = 1, sampl

Translating:  36%|███▌      | 2914/8065 [00:00<00:00, 5222.50it/s]

Translation error: translate_batch(): incompatible function arguments. The following argument types are supported:
    1. (self: ctranslate2._ext.Translator, source: List[List[str]], target_prefix: Optional[List[Optional[List[str]]]] = None, *, max_batch_size: int = 0, batch_type: str = 'examples', asynchronous: bool = False, beam_size: int = 2, patience: float = 1, num_hypotheses: int = 1, length_penalty: float = 1, coverage_penalty: float = 0, repetition_penalty: float = 1, no_repeat_ngram_size: int = 0, disable_unk: bool = False, suppress_sequences: Optional[List[List[str]]] = None, end_token: Optional[Union[str, List[str], List[int]]] = None, return_end_token: bool = False, prefix_bias_beta: float = 0, max_input_length: int = 1024, max_decoding_length: int = 256, min_decoding_length: int = 1, use_vmap: bool = False, return_scores: bool = False, return_attention: bool = False, return_alternatives: bool = False, min_alternative_expansion_prob: float = 0, sampling_topk: int = 1, sampl

Translating:  50%|████▉     | 4025/8065 [00:00<00:00, 4874.30it/s]

Translating:  59%|█████▉    | 4796/8065 [00:00<00:00, 5176.48it/s]

Translation error: translate_batch(): incompatible function arguments. The following argument types are supported:
    1. (self: ctranslate2._ext.Translator, source: List[List[str]], target_prefix: Optional[List[Optional[List[str]]]] = None, *, max_batch_size: int = 0, batch_type: str = 'examples', asynchronous: bool = False, beam_size: int = 2, patience: float = 1, num_hypotheses: int = 1, length_penalty: float = 1, coverage_penalty: float = 0, repetition_penalty: float = 1, no_repeat_ngram_size: int = 0, disable_unk: bool = False, suppress_sequences: Optional[List[List[str]]] = None, end_token: Optional[Union[str, List[str], List[int]]] = None, return_end_token: bool = False, prefix_bias_beta: float = 0, max_input_length: int = 1024, max_decoding_length: int = 256, min_decoding_length: int = 1, use_vmap: bool = False, return_scores: bool = False, return_attention: bool = False, return_alternatives: bool = False, min_alternative_expansion_prob: float = 0, sampling_topk: int = 1, sampl

KeyboardInterrupt: 

In [ ]:
### Eval original model 

# def translate(model, tokenizer, text, device):
#     inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=150).to(device)
#     translated = model.generate(**inputs)
#     return tokenizer.batch_decode(translated, skip_special_tokens=True)

# def calculate_bleu(references, hypotheses):
#     bleu = BLEU()
#     return bleu.corpus_score(hypotheses, [references]).score

# def validate_model(model_name, dataset_name, split):
#     device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
#     print(f"Using device: {device}")

#     # Load model and tokenizer
#     tokenizer = AutoTokenizer.from_pretrained(model_name)
#     model = AutoModelForSeq2SeqLM.from_pretrained(model_name).to(device)

#     # Load dataset
#     dataset = load_dataset(dataset_name, split=split)

#     # Translate and calculate BLEU score
#     hypotheses = []
#     references = []

#     for batch in tqdm(dataset, desc="Translating"):
#         source_text = batch['translation']['dyu']  # Adjust this based on your dataset's column names
#         reference = batch['translation']['fr']  # Adjust this based on your dataset's column names
        
#         translation = translate(model, tokenizer, source_text, device)[0]
#         # print(reference)
#         # print(translation)
        
#         hypotheses.append(translation)
#         references.append(reference)
#         # break

#     bleu_score = calculate_bleu(references, hypotheses)
#     print(f"BLEU Score: {bleu_score:.2f}")

# # Run validation with GPU
# # validate_model(model_checkpoint, "uvci/Koumankan_mt_dyu_fr", use_gpu=True)

# # Run validation without GPU
# validate_model(new_model_path, "uvci/Koumankan_mt_dyu_fr", "validation")